# Импорт библиотек

In [1]:
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport
import re

# Загружаем данные соревнования

In [2]:
data_raw = pd.read_csv('test.csv.zip')

In [3]:
data_raw.head(2).T

0  \
bodyType                                                        лифтбек   
brand                                                             SKODA   
car_url               https://auto.ru/cars/used/sale/skoda/octavia/1...   
color                                                             синий   
complectation_dict                                                  NaN   
description           Все автомобили, представленные в продаже, прох...   
engineDisplacement                                              1.2 LTR   
enginePower                                                     105 N12   
equipment_dict        {"engine-proof":true,"tinted-glass":true,"airb...   
fuelType                                                         бензин   
image                 https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...   
mileage                                                           74000   
modelDate                                                          2013   
model_info            {"code":"OCTAVIA","name":"Octavia","ru_name":"...   
model_name                                                      OCTAVIA   
name                                                 1.2 AMT (105 л.с.)   
numberOfDoors                                                         5   
parsing_unixtime                                             1603226273   
priceCurrency                                                       RUB   
productionDate                                                     2014   
sell_id                                                      1100575026   
super_gen             {"id":"10373605","displacement":1197,"engine_t...   
vehicleConfiguration                                 LIFTBACK ROBOT 1.2   
vehicleTransmission                                    роботизированная   
vendor                                                         EUROPEAN   
Владельцы                                                   3 или более   
Владение                                                            NaN   
ПТС                                                            Оригинал   
Привод                                                         передний   
Руль                                                              Левый   
Состояние                                            Не требует ремонта   
Таможня                                                      Растаможен   

                                                                      1  
bodyType                                                        лифтбек  
brand                                                             SKODA  
car_url               https://auto.ru/cars/used/sale/skoda/octavia/1...  
color                                                            чёрный  
complectation_dict                                                  NaN  
description           ЛОТ: 01217195\nАвтопрага Север\nДанный автомоб...  
engineDisplacement                                              1.6 LTR  
enginePower                                                     110 N12  
equipment_dict        {"cruise-control":true,"asr":true,"esp":true,"...  
fuelType                                                         бензин  
image                 https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...  
mileage                                                           60563  
modelDate                                                          2017  
model_info            {"code":"OCTAVIA","name":"Octavia","ru_name":"...  
model_name                                                      OCTAVIA  
name                                                  1.6 MT (110 л.с.)  
numberOfDoors                                                         5  
parsing_unixtime                                             1603226277  
priceCurrency                                                       RUB  
productionDate                                                     2017  
sell_id                                 

In [4]:
data_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34686 entries, 0 to 34685
Data columns (total 32 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   bodyType              34686 non-null  object
 1   brand                 34686 non-null  object
 2   car_url               34686 non-null  object
 3   color                 34686 non-null  object
 4   complectation_dict    6418 non-null   object
 5   description           34686 non-null  object
 6   engineDisplacement    34686 non-null  object
 7   enginePower           34686 non-null  object
 8   equipment_dict        24690 non-null  object
 9   fuelType              34686 non-null  object
 10  image                 34686 non-null  object
 11  mileage               34686 non-null  int64 
 12  modelDate             34686 non-null  int64 
 13  model_info            34686 non-null  object
 14  model_name            34686 non-null  object
 15  name                  34686 non-null

In [5]:
# есть ли полные дубли?
data_raw['sell_id'].nunique() < data_raw.shape[0]

False

In [6]:
data_raw_profile = ProfileReport(data_raw, title="Pandas Profiling Report")
data_raw_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Что видно из датасета:
- стоимости нет, значит использовать этот датасет как обучающий нельзя, совсем
- почти все признаки - категориальные
- пропусков в целом мало, но есть
- цены только в рублях
- состояние у всех одинаково заявлено
- все растаможены
- ссылка на страницу не даст информации
- complectation_dict - чёрти что и почти одни пропуски
- description - можно попробовать определить частник или салон
- image - есть не уникальные
- Владение - очень много пропусков
- есть названия признаков на русском, значит надо привести все к единому виду
- есть много признаков с описанием словами

# Предобработка v2

## Копируем основу

In [7]:
# удалим бесполезное
data_1 = data_raw.drop(columns=['priceCurrency', 'Состояние', 'Таможня',
                       'car_url', 'complectation_dict', 'image', 'model_info', 
                       'Владение'])

In [8]:
# удалим требующее обработки, добавим потом из data_raw
data_1.drop(columns=['parsing_unixtime', 'ПТС', 'Руль', 'model_name',
                     'equipment_dict', 'name', 'super_gen', 'vendor', 
                     'sell_id', 'vehicleConfiguration'], inplace=True)
# оставим description для CatBoost
# super_gen - шикарный признак для разбора, но не имеет аналога в обучающем датасете :(
# model пойдёт в сборный признак

## Правим названия

In [9]:
# приведем названия к единому стилю
rule_rename = {'bodyType': 'body_type',
               'engineDisplacement': 'engine_displacement',
               'enginePower': 'engine_power',
               'fuelType': 'fuel_type',
               'modelDate': 'model_year',
               'numberOfDoors': 'n_doors',
               'productionDate': 'production_year',
               'vehicleConfiguration': 'vehicle_configuration',
               'vehicleTransmission': 'vehicle_transmission',
               'Владельцы': 'n_owners',
               'Привод': 'drive_type'}
data_1.rename(columns=rule_rename, inplace=True)

## Простые обработки признаков

In [10]:
# пока что не знаю, зачем нужен этот признак

# дату парсинга в формат DateTime
# data_1['parsing_dt'] = pd.to_datetime(data_raw['parsing_unixtime'], origin='unix', unit='s')

In [11]:
# ПТС - это бинарный признак, оригинал или дубликат
data_1['is_original_techpass'] = data_raw['ПТС'].apply(lambda x: 1 if x in ['ORIGINAL', 'Оригинал'] else 0).astype('int8')

In [12]:
# Руль - это бинарный признак, левый или правый
data_1['is_lefthand_drive'] = data_raw['Руль'].apply(lambda x: 1 if x in ['LEFT', 'Левый'] else 0).astype('int8')

In [13]:
# сделаем объем двигателя числом
engine_displacement_re = data_1['engine_displacement'].apply(lambda x : re.match('\d\.\d', x))
data_1['engine_displacement'] = engine_displacement_re.apply(lambda x: float(x.group(0)) if x is not None else np.NaN)

In [14]:
# сделаем мощность двигателя числом
engine_power_re = data_1['engine_power'].apply(lambda x : re.match('\d*', x))
data_1['engine_power'] = engine_power_re.apply(lambda x: float(x.group(0)) if x is not None else np.NaN)

In [15]:
# укрупним категории типа кузова
def generic_body_type(raw_body_type):
    """
    Функция ищет ключевые слова в описании кузова и возвращает тип кузова
    """
    result = raw_body_type
    body_type = raw_body_type.lower()
    generic_dict = {'лифтбек': 'лифтбек',
                    'фастбек': 'лифтбек',
                    'седан': 'седан',
                    'внедорожник': 'внедорожник',
                    'хэтчбек': 'хэтчбек',
                    'универсал': 'универсал',
                    'пикап': 'пикап',
                    'купе': 'купе',
                    'кабриолет': 'кабриолет',
                    'родстер': 'родстер',
                    'тарга': 'родстер',
                    'вэн': 'минивэн',
                    'лимузин': 'лимузин',
                    'фургон': 'фургон'}
    for keyword in generic_dict.keys():
        if body_type.find(keyword) >= 0:
            result = generic_dict[keyword]
            break
    return result

data_1['body_type'] = data_1['body_type'].fillna(value='unknown').apply(generic_body_type)
data_1['body_type'].unique()

array(['лифтбек', 'внедорожник', 'хэтчбек', 'седан', 'минивэн',
       'универсал', 'пикап', 'купе', 'кабриолет', 'родстер', 'лимузин',
       'фургон'], dtype=object)

In [16]:
# назовём цвет кузова
# https://hysy.org/colors/
def generic_color(raw_color):
    """
    Функция проверяет цвет и даёт ему название
    """
    result = raw_color
    generic_dict = {'040001': 'чёрный',
                    'EE1D19': 'красный',
                    '0000CC': 'синий',
                    'CACECB': 'серый',
                    '007F00': 'зелёный',
                    'FAFBFB': 'белый',
                    '97948F': 'серый',
                    '22A0F8': 'синий',
                    '660099': 'фиолетовый',
                    '200204': 'коричневый',
                    'C49648': 'бежевый',
                    'DEA522': 'жёлтый',
                    '4A2197': 'фиолетовый',
                    'FFD600': 'жёлтый',
                    'FF8649': 'розовый',
                    'FFC0CB': 'розовый',
                    'пурпурный': 'фиолетовый',
                    'голубой': 'синий',
                    'золотистый': 'жёлтый',
                    'серебристый': 'серый',
                    'оранжевый': 'жёлтый'}
    for keyword in generic_dict.keys():
        if raw_color.find(keyword) >= 0:
            result = generic_dict[keyword]
            break
    return result

data_1['color'] = data_1['color'].fillna(value='unknown').apply(generic_color)
data_1['color'].unique()

array(['синий', 'чёрный', 'серый', 'коричневый', 'белый', 'фиолетовый',
       'бежевый', 'красный', 'зелёный', 'жёлтый', 'розовый'], dtype=object)

In [17]:
# назовём тип КПП
def generic_transmission(raw_gearbox):
    """
    Функция даёт название КПП
    """
    result = raw_gearbox
    generic_dict = {'MECHANICAL': 'механика',
                    'AUTOMATIC': 'автомат',
                    'ROBOT': 'робот',
                    'VARIATOR': 'вариатор',
                    'роботизированная': 'робот',
                    'механическая': 'механика',
                    'автоматическая': 'автомат',
                    'вариатор': 'вариатор'
                   }
    for keyword in generic_dict.keys():
        if raw_gearbox.find(keyword) >= 0:
            result = generic_dict[keyword]
            break
    return result

data_1['vehicle_transmission'] = data_1['vehicle_transmission'].fillna(value='unknown').apply(generic_transmission)
data_1['vehicle_transmission'].unique()

array(['робот', 'механика', 'автомат', 'вариатор'], dtype=object)

In [18]:
# назовём количество владельцев
def generic_owners(raw_owners):
    """
    Функция даёт название КПП
    """
    result = str(raw_owners)
    generic_dict = {'1': '1',
                    '2': '2',
                    '3': '3+',
                   }
    for keyword in generic_dict.keys():
        if str(raw_owners).find(keyword) >= 0:
            result = generic_dict[keyword]
            break
    return result

data_1['n_owners'] = data_1['n_owners'].fillna(value='unknown').apply(generic_owners)
data_1['n_owners'].unique()

array(['3+', '1', '2'], dtype=object)

## Более сложные признаки

In [19]:
# соберём марку и модель в один признак
data_1['full_model_name'] = (data_raw['brand'] + ' ' + data_raw['model_name']).str.lower()
data_1['full_model_name'].unique()

array(['skoda octavia', 'skoda superb', 'skoda octavia_rs', 'skoda yeti',
       'skoda kodiaq', 'skoda rapid', 'skoda fabia', 'skoda roomster',
       'skoda felicia', 'skoda karoq', 'skoda fabia_rs', 'skoda 120',
       'skoda 100_series', 'skoda favorit', 'skoda popular', 'audi q5',
       'audi r8', 'audi q7', 'audi q3', 'audi a4', 'audi a3', 'audi a5',
       'audi a6', 'audi rs7', 'audi s6', 'audi rs6', 'audi allroad',
       'audi tt', 'audi s5', 'audi s8', 'audi a1', 'audi a8', 'audi 80',
       'audi a7', 'audi rsq3', 'audi rs3', 'audi a4_allroad', 'audi q8',
       'audi 100', 'audi sq5', 'audi s4', 'audi tt_rs', 'audi rs4',
       'audi s7', 'audi rs5', 'audi 90', 'audi coupe', 'audi a2',
       'audi tts', 'audi 920', 'audi s3', 'audi 200', 'audi v8',
       'audi e_tron', 'honda cr_v', 'honda accord', 'honda pilot',
       'honda civic', 'honda odyssey', 'honda stream', 'honda crosstour',
       'honda elysion', 'honda element', 'honda ridgeline', 'honda fit',
       'hond

# Посмотрим на результат предобработки

In [20]:
data_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34686 entries, 0 to 34685
Data columns (total 17 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   body_type             34686 non-null  object 
 1   brand                 34686 non-null  object 
 2   color                 34686 non-null  object 
 3   description           34686 non-null  object 
 4   engine_displacement   34631 non-null  float64
 5   engine_power          34686 non-null  float64
 6   fuel_type             34686 non-null  object 
 7   mileage               34686 non-null  int64  
 8   model_year            34686 non-null  int64  
 9   n_doors               34686 non-null  int64  
 10  production_year       34686 non-null  int64  
 11  vehicle_transmission  34686 non-null  object 
 12  n_owners              34686 non-null  object 
 13  drive_type            34686 non-null  object 
 14  is_original_techpass  34686 non-null  int8   
 15  is_lefthand_drive  

In [21]:
data_1_profile = ProfileReport(data_1, title="Data_EDA_v1 Profiling Report")
data_1_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Сохраним результат предобработки

In [22]:
compression_opts = dict(method='zip', archive_name='EDAv2_Test.csv')  
data_1.to_csv('EDAv2_Test.zip', index=False, compression=compression_opts)